# Welcome to Jupyter!

This repo contains an introduction to [Jupyter](https://jupyter.org) and [IPython](https://ipython.org).

Outline of some basics:

* [Notebook Basics](../examples/Notebook/Notebook%20Basics.ipynb)
* [IPython - beyond plain python](../examples/IPython%20Kernel/Beyond%20Plain%20Python.ipynb)
* [Markdown Cells](../examples/Notebook/Working%20With%20Markdown%20Cells.ipynb)
* [Rich Display System](../examples/IPython%20Kernel/Rich%20Output.ipynb)
* [Custom Display logic](../examples/IPython%20Kernel/Custom%20Display%20Logic.ipynb)
* [Running a Secure Public Notebook Server](../examples/Notebook/Running%20the%20Notebook%20Server.ipynb#Securing-the-notebook-server)
* [How Jupyter works](../examples/Notebook/Multiple%20Languages%2C%20Frontends.ipynb) to run code in different languages.

You can also get this tutorial and run it on your laptop:

    git clone https://github.com/ipython/ipython-in-depth

Install IPython and Jupyter:

with [conda](https://www.anaconda.com/download):

    conda install ipython jupyter

with pip:

    # first, always upgrade pip!
    pip install --upgrade pip
    pip install --upgrade ipython jupyter

Start the notebook in the tutorial directory:

    cd ipython-in-depth
    jupyter notebook

In [51]:
import sys
#!{sys.executable} -m pip install SPARQLWrapper
from SPARQLWrapper import SPARQLWrapper, JSON
import pandas as pd
import numpy as np
import datetime
import func_lib

endpoint_url = "https://query.wikidata.org/sparql"
item = "item"


class Relation:
    """
    The class returned when createRelation is called.
    It contains string field with query.
    We call Relation.query when we need to do the query.
    """

    def __init__(self, entity_id: str, property_id: str, isSubject: bool, rowVerbose: bool,
                 colVerbose: bool, time_property: str, time: str, name: str, label: bool, limit=10000):
        self.entity_id = entity_id
        self.query_str = ""
        self.dic = {}
        self.result_dic = {"Entity ID": []}
        self.df = pd.DataFrame()
        self.count = 0
        self.time_property = time_property
        self.time = time
        self.limit = limit
        self.focus = "Entity ID"
        if property_id:
            self.extend(property_id, isSubject, name, rowVerbose, colVerbose, limit, time_property, time, label)

    def generate_html(self, name: str):
        html = (self.df).to_html()
        text_file = open(name, "w", encoding='utf-8')
        text_file.write(html)
        text_file.close()

    def query(self, require=None):
        if self.query_str == "":
            self.result_dic = {"Entity ID": ['http://www.wikidata.org/entity/' + str(self.entity_id)]}
            return self.result_dic
        results = get_results(endpoint_url, self.query_str)
        result_dict = {"Entity ID": ['http://www.wikidata.org/entity/' + str(self.entity_id)]}
        for i in range(1, self.count + 1):
            result_dict[self.dic[i]["name"] + '_' + self.dic[i]['property_id']] = []
            if self.dic[i]["colVerbose"]:
                result_dict[self.dic[i]["name"] + '_rank_' + self.dic[i]['property_id'] + '_rank'] = []
                for key, value in self.dic[i]["property_name_dic"].items():
                    result_dict[
                        self.dic[i]["name"] + "_" + value + '_' + self.dic[i]['property_id'] + '_' + str(key)] = []
                for key, value in self.dic[i]["ref_dic"].items():
                    result_dict[self.dic[i]["name"] + "_ref_" + self.dic[i]['property_id'] + '_' + str(key)] = []

            if self.dic[i]["label"]:
                result_dict[self.dic[i]["name"] + '_' + self.dic[i]['property_id'] + 'Label'] = []

        for result in results['results']['bindings']:
            for key, value in result_dict.items():
                if key in result.keys():
                    result_dict[key].append(result[key]['value'])
                else:
                    result_dict[key].append('NA')
        result_dict["Entity ID"] = ['http://www.wikidata.org/entity/' + str(self.entity_id)] * len(
            result_dict[self.dic[self.count]["name"] + '_' + self.dic[self.count]["property_id"]])
        self.result_dic = result_dict
        self.df = pd.DataFrame.from_dict(self.result_dic)
        for i in range(1, self.count + 1):
            if self.dic[i]["colVerbose"] and not self.dic[i]["rowVerbose"]:
                col = self.dic[i]['name'] + '_rank_' + self.dic[i]['property_id'] + '_rank'
                if any(self.df[col] == 'http://wikiba.se/ontology#PreferredRank'):
                    self.df = self.df.loc[self.df[col] == 'http://wikiba.se/ontology#PreferredRank']
                else:
                    self.df = self.df.loc[self.df[col] == 'http://wikiba.se/ontology#NormalRank']
#         if require is not None:
#             for r in require:
#                 self.df = self.df.loc[self.df[r] != 'NA']
        self.df = pd.DataFrame(data=self.df)
#         if self.df.shape[0] >= 10000:
#             print("Warning: Your query leads to too many results. Only 10,000 returned.")
        return self.df

    def extend(self, property_id: str, isSubject: bool, name: str, rowVerbose=False, colVerbose=False, limit=None,
               time_property=None, time=None, search=None, label=False):
        self.count += 1
        self.dic[self.count] = {}
        self.dic[self.count]["name"] = name
        self.dic[self.count]["focus"] = self.focus
        self.dic[self.count]["property_id"] = property_id
        self.dic[self.count]["isSubject"] = isSubject
        self.dic[self.count]["limit"] = limit
        self.dic[self.count]["rowVerbose"] = rowVerbose
        self.dic[self.count]["colVerbose"] = colVerbose
        self.dic[self.count]['time_property'] = time_property
        self.dic[self.count]['time'] = time
        self.dic[self.count]['search'] = search
        self.dic[self.count]['label'] = label
        if rowVerbose or colVerbose:
            self.dic[self.count]["property_name_dic"], self.dic[self.count][
                "ref_dic"] = self.search_property_for_verbose()
        if time_property and time:
            self.time_property = time_property
            self.time = time
        if limit:
            self.limit = limit
        self.query_str = self.define_query_relation()

    def changeFocus(self, name="Entity ID"):
        self.focus = name
    
    def extendWithFunction(self, columns, func, name, param=None, dim=-1):
        if dim == 1:
            if isinstance(columns, list):
                if param is not None:
                    if isinstance(param, list):
                        self.df[name] = self.df[columns].apply(lambda x: func(*x, *param), axis=1)
                    else:
                        self.df[name] = self.df[columns].apply(lambda x: func(*x, param), axis=1)
                else:
                    self.df[name] = self.df[columns].apply(lambda x: func(*x), axis=1)
            else:
                if param is not None:
                    if isinstance(param, list):
                        self.df[name] = self.df[columns].apply(lambda x: func(x, *param), axis=1)
                    else:
                        self.df[name] = self.df[columns].apply(lambda x: func(x, param), axis=1)
                else:
                    self.df[name] = self.df[columns].apply(func, axis=1)
        elif dim == 0:
            if isinstance(columns, list):
                if param is not None:
                    if isinstance(param, list):
                        func(self.df[columns], axis=0)
                    else:
                        func(self.df[columns], axis=0)
                else:
                    func(self.df[columns], axis=0)
            else:
                if param is not None:
                    if isinstance(param, list):
                        func(self.df[columns], axis=0)
                    else:
                        func(self.df[columns], axis=0)
                else:
                    func(self.df[columns], axis=0)
                
        else:
            if isinstance(columns, list):
                if param is not None:
                    if isinstance(param, list):
                        self.df = func(self.df, name, *columns, *param)
                    else:
                        self.df = func(self.df, name, *columns, param)
                else:
                    self.df = func(self.df, name, *columns)
            else:
                if param is not None:
                    if isinstance(param, list):
                        self.df = func(self.df, name, columns, *param)
                    else:
                        self.df = func(self.df, name, columns, param)
                else:
                    self.df = func(self.df, name, columns)
        
#         if not entity:
#             if isinstance(columns, list):
#                 if param is not None:
#                     if isinstance(param, list):
#                         self.df = func(self.df, name, *columns, *param)
#                     else:
#                         self.df = func(self.df, name, *columns, param)
#                 else:
#                     self.df = func(self.df, name, *columns)
#             else:
#                 if param is not None:
#                     if isinstance(param, list):
#                         self.df = func(self.df, name, columns, *param)
#                     else:
#                         self.df = func(self.df, name, columns, param)
#                 else:
#                     self.df = func(self.df, name, columns)
#         else:
#             if isinstance(columns, list):
#                 if param is not None:
#                     if isinstance(param, list):
#                         self.df[name] = self.df[columns].apply(lambda x: func(*x, *param), axis=1)
#                     else:
#                         self.df[name] = self.df[columns].apply(lambda x: func(*x, param), axis=1)
#                 else:
#                     self.df[name] = self.df[columns].apply(lambda x: func(*x), axis=1)
#             else:
#                 if param is not None:
#                     if isinstance(param, list):
#                         self.df[name] = self.df[columns].apply(lambda x: func(x, *param), axis=1)
#                     else:
#                         self.df[name] = self.df[columns].apply(lambda x: func(x, param), axis=1)
#                 else:
#                     self.df[name] = self.df[columns].apply(func, axis=1)
#         else:
#             if type(func) == str:
#                 if func.startswith('F'):
#                     try:
#                         func_id = int(func[1:])
#                         if func_id >= func_lib.func_num():
#                             print("Not available.")
#                         else:
#                             if isinstance(objcolumn, list):
#                                 self.df[name] = self.df[columns].apply(lambda x: func_lib.func_list[func_id](*x), axis=1)
#                             else:
#                                 self.df[name] = self.df[columns].apply(func_lib.func_list[func_id])
#                     except:
#                         raise Exception("Not a valid function id, a valid function id should be 'Fn', n is an integer.")
#                 else:
#                     raise Exception("Not a valid function id, a valid function id should be 'Fn', n is an integer.")
#             else:
#                 if isinstance(columns, list):
#                     self.df[name] = self.df[columns].apply(lambda x: func(*x), axis=1)
#                 else:
#                     self.df[name] = self.df[columns].apply(func)

    def define_query_relation(self):
        rdf_triple, time_filter, limit_statement = """""", """""", """"""
        if self.count < 1:
            return None
        focusChanges = 0
        for i in range(1, self.count + 1):
            if self.dic[i]["rowVerbose"] or self.dic[i]["colVerbose"]:
                if self.dic[i]["search"] is None and not self.dic[i]["isSubject"]:
                        rdf_triple += """OPTIONAL {"""
                if self.dic[i]["focus"] == "Entity ID":
#                     if self.dic[i]["search"] is None:
#                         rdf_triple += """OPTIONAL {"""
                    rdf_triple += """wd:""" + self.entity_id + """ p:""" + self.dic[i][
                        'property_id'] + """ ?statement_""" + str(i) + """. """ \
                                  + """?statement_""" + str(i) + """ ps:""" + self.dic[i][
                                      'property_id'] + """ ?""" + \
                                  self.dic[i]['name'] \
                                  + """_""" + self.dic[i]['property_id'] + """. """
                else:
                    rdf_triple += """?""" + self.dic[i]["focus"] + """ p:""" + self.dic[i][
                        'property_id'] + """ ?statement_""" + str(i) + """. """ \
                                  + """?statement_""" + str(i) + """ ps:""" + self.dic[i][
                                      'property_id'] + """ ?""" + \
                                  self.dic[i]['name'] \
                                  + """_""" + self.dic[i]['property_id'] + """. """
                for key, value in self.dic[i]["property_name_dic"].items():
                    rdf_triple += """OPTIONAL { """ + """?statement_""" + str(i) + """ pq:""" + str(key) \
                                  + """ ?""" + self.dic[i]['name'] + """_""" + value + """_""" + self.dic[i][
                                      'property_id'] + """_""" + str(key) + """.} """
                for key, value in self.dic[i]["ref_dic"].items():
                    rdf_triple += """OPTIONAL { ?statement_""" + str(
                        i) + """ prov:wasDerivedFrom ?refnode_""" + str(
                        i) + """. ?refnode_""" + str(i) \
                                  + """ pr:""" + str(key) + """ ?""" + self.dic[i]['name'] + """_ref_""" + \
                                  self.dic[i][
                                      'property_id'] + """_""" + str(key) + """.} """
                rdf_triple += """OPTIONAL { ?statement_""" + str(i) + """ wikibase:rank ?""" + self.dic[i][
                    'name'] + """_rank_""" + self.dic[i]['property_id'] + """_rank. } """
            # none-verbose version
            else:
                if self.dic[i]["focus"] == "Entity ID":
                    if self.dic[i]["isSubject"]:
#                         if self.dic[i]["search"] is None:
#                             rdf_triple += """OPTIONAL {"""
                        rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                            'property_id'] + """ wdt:""" + self.dic[i][
                                          "property_id"] + """ wd:""" + self.entity_id + """. """
                    else:
                        if self.dic[i]["search"] is None:
                            rdf_triple += """OPTIONAL {"""
                        rdf_triple += """wd:""" + self.entity_id + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + \
                                      self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """. """
                else:
                    if self.dic[i]["isSubject"]:
#                         if self.dic[i]["search"] is None:
#                             rdf_triple += """OPTIONAL {"""
                        rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                            'property_id'] + """ wdt:""" + self.dic[i]["property_id"] + """ ?""" + self.dic[i][
                                          'focus'] + """. """
                    else:
                        if self.dic[i]["search"] is None:
                            rdf_triple += """OPTIONAL {"""
                        rdf_triple += """?""" + self.dic[i]['focus'] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                          'property_id'] + """. """
            if not self.dic[i]["isSubject"]:
                if i < self.count and self.dic[i]["focus"] != self.dic[i + 1]["focus"] and self.dic[i]["search"] is None:
                    focusChanges += 1
                elif self.dic[i]["search"] is None:
                    rdf_triple += """} """
        for i in range(focusChanges):
            rdf_triple += """} """
        for i in range(1, self.count + 1):
            if self.dic[i]['search'] is not None and self.dic[i]["search"] != '!NA':
                if isinstance(self.dic[i]['search'], tuple):
                    if isinstance(self.dic[i]['search'][0], str):
                        rdf_triple += """FILTER (YEAR(?""" + self.dic[i]['name'] + """_""" + self.dic[i][
                            'property_id'] + """) >= """ + \
                                      self.dic[i]['search'][0] + """ && YEAR(?""" + self.dic[i]['name'] + \
                                      """_""" + self.dic[i]['property_id'] + """) <= """ + self.dic[i]['search'][
                                          1] + """) """
                    else:
                        rdf_triple += """FILTER (?""" + self.dic[i]['name'] + """_""" + self.dic[i]['property_id'] + \
                                      """ >= """ + str(self.dic[i]['search'][0]) + """ && ?""" + self.dic[i]['name'] + \
                                      """_""" + self.dic[i]['property_id'] + """ <= """ + str(
                            self.dic[i]['search'][1]) + """) """
                else:
                    rdf_triple += """FILTER (?""" + self.dic[i]['name'] + """_""" + self.dic[i][
                        'property_id'] + """ = """ + \
                                  """wd:""" + self.dic[i]['search'] + """) """
        if self.time_property is not None:
            time_filter = """?""" + self.dic[1]["name"] + """ p:""" + self.time_property + """ ?pubdateStatement.	
                          ?pubdateStatement ps:""" + self.time_property + """ ?date	
                          FILTER (YEAR(?date) = """ + self.time + """)"""
        if self.limit is not None:
            limit_statement = """LIMIT """ + str(self.limit)
        label_statement = """Service wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en" }"""
        query = """SELECT DISTINCT"""
        for i in range(1, self.count + 1):
            if self.dic[i]["rowVerbose"] or self.dic[i]["colVerbose"]:
                query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id']
                if self.dic[i]["label"]:
                    query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """Label"""
                for key, value in self.dic[i]["property_name_dic"].items():
                    query += """ ?""" + self.dic[i]["name"] + """_""" + value + """_""" + self.dic[i][
                        'property_id'] + """_""" + str(key)
                for key, value in self.dic[i]["ref_dic"].items():
                    query += """ ?""" + self.dic[i]["name"] + """_ref_""" + self.dic[i]['property_id'] + """_""" + str(
                        key)
                query += """ ?""" + self.dic[i]["name"] + """_rank_""" + self.dic[i]['property_id'] + """_rank"""
            else:
                query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id']
                if self.dic[i]["label"]:
                    query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """Label"""
        query += """ WHERE {""" + rdf_triple + time_filter + label_statement + """} """ + limit_statement
        return query

    def search_property_for_verbose(self):
        property_to_name = {}
        ref_to_name = {}
        rdf_triple, time_filter, limit_statement = """""", """""", """"""
        if self.dic[self.count]["rowVerbose"] or self.dic[self.count]["colVerbose"]:
            for i in range(1, self.count):
                if self.dic[i]["focus"] == "Entity ID":
                    if self.dic[i]["isSubject"]:
                        rdf_triple += """?""" + self.dic[i]["name"] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ wd:""" + self.entity_id + """ ."""
                    else:
                        rdf_triple += """wd:""" + self.entity_id + """ wdt:""" + self.dic[i]["property_id"] + """ ?""" + \
                                      self.dic[i]["name"] + """ ."""
                else:
                    last = self.dic[i]["focus"].rfind('_')
                    focus = self.dic[i]["focus"][:last]
                    if self.dic[i]["isSubject"]:
                        rdf_triple += """?""" + self.dic[i]["name"] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + focus + """ ."""
                    else:
                        rdf_triple += """?""" + focus + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + self.dic[i]["name"] + """ ."""
            if self.dic[self.count]["focus"] == "Entity ID":
                rdf_triple += """wd:""" + self.entity_id + """ p:""" + self.dic[self.count][
                    'property_id'] + """ ?statement.""" + \
                              """?statement """ + """ps:""" + self.dic[self.count]['property_id'] + """ ?item.""" + \
                              """?statement """ + """?pq """ + """?obj.""" + \
                              """?qual wikibase:qualifier ?pq.""" + \
                              """OPTIONAL{ ?statement prov:wasDerivedFrom ?refnode. ?refnode ?pr ?r.}"""
            else:
                last = self.dic[self.count]["focus"].rfind('_')
                focus = self.dic[self.count]["focus"][:last]
                rdf_triple += """?""" + focus + """ p:""" + self.dic[self.count][
                    'property_id'] + """ ?statement.""" + \
                              """?statement """ + """ps:""" + self.dic[self.count]['property_id'] + """ ?item.""" + \
                              """?statement """ + """?pq """ + """?obj.""" + \
                              """?qual wikibase:qualifier ?pq.""" + \
                              """OPTIONAL{ ?statement prov:wasDerivedFrom ?refnode. ?refnode ?pr ?r.}"""
        if self.time_property is not None:
            time_filter = """?""" + self.dic[1]["name"] + """ p:""" + self.time_property + """ ?pubdateStatement.	
                                  ?pubdateStatement ps:""" + self.time_property + """ ?date	
                                  FILTER (YEAR(?date) = """ + self.time + """)"""
        if self.limit is not None:
            limit_statement = """LIMIT """ + str(self.limit)
        label_statement = """Service wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en" }"""
        query = """SELECT DISTINCT """
        if self.dic[self.count]["rowVerbose"] or self.dic[self.count]["colVerbose"]:
            query += """?item""" + """ ?qual""" + """ ?qualLabel""" + """ ?obj """ + """?pr ?prLabel"""
            query += """ WHERE {""" + rdf_triple + time_filter + label_statement + """} """ + limit_statement
            query_result = get_results(endpoint_url, query)
            for result in query_result['results']['bindings']:
                if 'qual' in result:
                    property_to_name[result['qual']['value'].split('/')[-1]] = result['qualLabel']['value'].replace(' ',
                                                                                                                    '_')
                if 'pr' in result:
                    ref_to_name[result['pr']['value'].split('/')[-1]] = result['prLabel']['value'].replace(' ', '_')
        else:
            query += """?""" + self.dic[self.count]["name"] + """ """
        return property_to_name, ref_to_name

    def __str__(self):
        return str(self.df)

    def __getattr__(self, col_name):
        if col_name in self.df.columns:
            return self.df[col_name]
        else:
            print(col_name + " has not been found.")
            return None


def createRelation(entity_id: str, property_id=None, isSubject=None, rowVerbose=None, colVerbose=None,
                   time_property=None, time=None, name=None, label=False, limit=None):
    if property_id and not name:
        print("Please specify the name of the first column")
        return None
    return Relation(entity_id, property_id, isSubject, rowVerbose, colVerbose, time_property, time, name, label, limit)

def get_Firstname(name: str):
    return name.split(' ')[0]

def get_Lastname(name: str):
    return name.split(' ')[-1]

def remove_prefix(text, prefix):
    if text.startswith(prefix):
        return text[len(prefix):]
    return text


def get_results(endpoint_url, query):
    user_agent = "WDQS-example Python/%s.%s" % (sys.version_info[0], sys.version_info[1])
    # TODO adjust user agent; see https://w.wiki/CX6
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    return sparql.query().convert()


def get_name(id: str):
    query = """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#> 	
                PREFIX wd: <http://www.wikidata.org/entity/> 	
                select  *	
                where {	
                wd:""" + id + """ rdfs:label ?label .	
                FILTER (langMatches( lang(?label), "EN" ) )	
                } 	
                LIMIT 1"""
    results = get_results(endpoint_url, query)
    result = ''
    for res in results["results"]["bindings"]:
        result = res['label']['value']
    return result


In [89]:
import sys
#!{sys.executable} -m pip install SPARQLWrapper
from SPARQLWrapper import SPARQLWrapper, JSON
import pandas as pd
import numpy as np
import datetime
import func_lib

endpoint_url = "https://query.wikidata.org/sparql"
item = "item"


class Relation:
    """
    The class returned when createRelation is called.
    It contains string field with query.
    We call Relation.query when we need to do the query.
    """

    def __init__(self, entity_id: str, property_id: str, linkDirection: str, rowVerbose: bool,
                 colVerbose: bool, time_property: str, time: str, name: str, label: bool, limit=10000, subclass=False, showid=False):
        self.entity_id = entity_id
        self.query_str = ""
        self.dic = {}
        self.result_dic = {"Entity ID": []}
        self.df = pd.DataFrame()
        self.count = 0
        self.time_property = time_property
        self.time = time
        self.limit = limit
        self.subclass = subclass
        self.focus = "Entity ID"
        if property_id:
            self.extend(property_id, linkDirection, name, rowVerbose, colVerbose, limit, time_property, time, label, subclass, showid)

    def generate_html(self, name: str):
        html = (self.df).to_html()
        text_file = open(name, "w", encoding='utf-8')
        text_file.write(html)
        text_file.close()

    def query(self):
        if self.query_str == "":
            self.result_dic = {"Entity ID": ['http://www.wikidata.org/entity/' + str(self.entity_id)]}
            return self.result_dic
        results = get_results(endpoint_url, self.query_str)
        result_dict = {"Entity ID": ['http://www.wikidata.org/entity/' + str(self.entity_id)]}
        for i in range(1, self.count + 1):
            result_dict[self.dic[i]["name"] + '_' + self.dic[i]['property_id']] = []
            if self.dic[i]["colVerbose"]:
                result_dict[self.dic[i]["name"] + '_rank_' + self.dic[i]['property_id'] + '_rank'] = []
                for key, value in self.dic[i]["property_name_dic"].items():
                    result_dict[
                        self.dic[i]["name"] + "_" + value + '_' + self.dic[i]['property_id'] + '_' + str(key)] = []
                for key, value in self.dic[i]["ref_dic"].items():
                    result_dict[self.dic[i]["name"] + "_ref_" + self.dic[i]['property_id'] + '_' + str(key)] = []

            if self.dic[i]["label"]:
                result_dict[self.dic[i]["name"] + '_' + self.dic[i]['property_id'] + 'Label'] = []

        for result in results['results']['bindings']:
            for key, value in result_dict.items():
                if key in result.keys():
                    result_dict[key].append(result[key]['value'])
                else:
                    result_dict[key].append('NA')
        result_dict["Entity ID"] = ['http://www.wikidata.org/entity/' + str(self.entity_id)] * len(
            result_dict[self.dic[self.count]["name"] + '_' + self.dic[self.count]["property_id"]])
        result_dict["Basic ID"] = [str(self.entity_id)] * len(
            result_dict[self.dic[self.count]["name"] + '_' + self.dic[self.count]["property_id"]])
        self.result_dic = result_dict
        self.df = pd.DataFrame.from_dict(self.result_dic)
        for i in range(1, self.count + 1):
            if self.dic[i]["colVerbose"] and not self.dic[i]["rowVerbose"]:
                col = self.dic[i]['name'] + '_rank_' + self.dic[i]['property_id'] + '_rank'
                if any(self.df[col] == 'http://wikiba.se/ontology#PreferredRank'):
                    self.df = self.df.loc[self.df[col] == 'http://wikiba.se/ontology#PreferredRank']
                else:
                    self.df = self.df.loc[self.df[col] == 'http://wikiba.se/ontology#NormalRank']
        for i in range(1, self.count + 1):
            if self.dic[i]["showid"]:
                self.df[self.dic[i]["name"] + '_' + self.dic[i]['property_id'] + '_basic'] = self.df[self.dic[i]["name"] + '_' + self.dic[i]['property_id']].apply(lambda x: x.split('/')[-1])
#         if require is not None:
#             for r in require:
#                 self.df = self.df.loc[self.df[r] != 'NA']
        self.df = pd.DataFrame(data=self.df)
#         if self.df.shape[0] >= 10000:
#             print("Warning: Your query leads to too many results. Only 10,000 returned.")
        return self.df

    def extend(self, property_id: str, linkDirection: str, name: str, rowVerbose=False, colVerbose=False, limit=None,
               time_property=None, time=None, search=None, label=False, subclass=False, showid=False):
        self.count += 1
        self.dic[self.count] = {}
        self.dic[self.count]["name"] = name
        self.dic[self.count]["focus"] = self.focus
        self.dic[self.count]["property_id"] = property_id
        if linkDirection == 'forward':
            self.dic[self.count]["isSubject"] = False
        elif linkDirection == 'backward':
            self.dic[self.count]["isSubject"] = True
        else:
            self.count -= 1
            raise Exception("Fail to extend! LinkDirection should be either forward or backward.")
        self.dic[self.count]["limit"] = limit
        self.dic[self.count]["rowVerbose"] = rowVerbose
        self.dic[self.count]["colVerbose"] = colVerbose
        self.dic[self.count]['time_property'] = time_property
        self.dic[self.count]['time'] = time
        self.dic[self.count]['search'] = search
        self.dic[self.count]['label'] = label
        self.dic[self.count]['subclass'] = subclass
        self.dic[self.count]['showid'] = showid
        # subclass is specific to P31, when subclass is true, we get intance of all subclasses of the entity
        if rowVerbose or colVerbose:
            self.dic[self.count]["property_name_dic"], self.dic[self.count][
                "ref_dic"] = self.search_property_for_verbose()
        if time_property and time:
            self.time_property = time_property
            self.time = time
        if limit:
            self.limit = limit
        self.query_str = self.define_query_relation()

    def changeFocus(self, name="Entity ID"):
        self.focus = name
    
    def extendWithFunctionHelper(self, columns, func, name, param, dim):
        if dim == 1:
            if isinstance(columns, list):
                if param is not None:
                    if isinstance(param, list):
                        self.df[name] = self.df[columns].apply(lambda x: func(*x, *param), axis=1)
                    else:
                        self.df[name] = self.df[columns].apply(lambda x: func(*x, param), axis=1)
                else:
                    self.df[name] = self.df[columns].apply(lambda x: func(*x), axis=1)
            else:
                if param is not None:
                    if isinstance(param, list):
                        self.df[name] = self.df[columns].apply(lambda x: func(x, *param), axis=1)
                    else:
                        self.df[name] = self.df[columns].apply(lambda x: func(x, param), axis=1)
                else:
                    self.df[name] = self.df[columns].apply(func, axis=1)
        elif dim == 0:
            if not isinstance(columns, list):
                columns = [columns]
            if param is not None:
                if isinstance(param, list):
                    return self.df[columns].apply(lambda x: func(x, *param), axis=0)
                        #return func(self.df[columns], *param, axis=0)
                else:
                    return self.df[columns].apply(lambda x: func(x, param), axis=0)
                        #return func(self.df[columns], param, axis=0)
            else:
                return self.df[columns].apply(lambda x: func(x), axis=0)
                    #return func(self.df[columns], axis=0)
#             else:
#                 if param is not None:
#                     if isinstance(param, list):
                        
#                         #return func(self.df[columns], axis=0)
#                     else:
#                         return func(self.df[columns], axis=0)
#                 else:
#                     return func(self.df[columns], axis=0)
                
        else:
            if isinstance(columns, list):
                if param is not None:
                    if isinstance(param, list):
                        self.df = func(self.df, name, *columns, *param)
                    else:
                        self.df = func(self.df, name, *columns, param)
                else:
                    self.df = func(self.df, name, *columns)
            else:
                if param is not None:
                    if isinstance(param, list):
                        self.df = func(self.df, name, columns, *param)
                    else:
                        self.df = func(self.df, name, columns, param)
                else:
                    self.df = func(self.df, name, columns)
    
    def extendWithFunction(self, columns, func, name=None, param=None, dim=-1):
        if type(func) == str:
            if func.startswith('F'):
                try:
                    func_id = int(func[1:])
                    if func_id >= func_lib.func_num():
                        print("Not available.")
                    else:
                        return self.extendWithFunctionHelper(columns, func, name, param, dim)
                except:
                    raise Exception("Not a valid function id, a valid function id should be 'Fn', n is an integer.")
            else:
                raise Exception("Not a valid function id, a valid function id should be 'Fn', n is an integer.")
        else:
            return self.extendWithFunctionHelper(columns, func, name, param, dim)

    def define_query_relation(self):
        rdf_triple, time_filter, limit_statement = """""", """""", """"""
        if self.count < 1:
            return None
        focusChanges = 0
        for i in range(1, self.count + 1):
            if self.dic[i]["rowVerbose"] or self.dic[i]["colVerbose"]:
                if self.dic[i]["search"] is None and not self.dic[i]["isSubject"]:
                        rdf_triple += """OPTIONAL {"""
                if self.dic[i]["focus"] == "Entity ID":
#                     if self.dic[i]["search"] is None:
#                         rdf_triple += """OPTIONAL {"""
                    rdf_triple += """wd:""" + self.entity_id + """ p:""" + self.dic[i][
                        'property_id'] + """ ?statement_""" + str(i) + """. """ \
                                  + """?statement_""" + str(i) + """ ps:""" + self.dic[i][
                                      'property_id'] + """ ?""" + \
                                  self.dic[i]['name'] \
                                  + """_""" + self.dic[i]['property_id'] + """. """
                else:
                    rdf_triple += """?""" + self.dic[i]["focus"] + """ p:""" + self.dic[i][
                        'property_id'] + """ ?statement_""" + str(i) + """. """ \
                                  + """?statement_""" + str(i) + """ ps:""" + self.dic[i][
                                      'property_id'] + """ ?""" + \
                                  self.dic[i]['name'] \
                                  + """_""" + self.dic[i]['property_id'] + """. """
                for key, value in self.dic[i]["property_name_dic"].items():
                    rdf_triple += """OPTIONAL { """ + """?statement_""" + str(i) + """ pq:""" + str(key) \
                                  + """ ?""" + self.dic[i]['name'] + """_""" + value + """_""" + self.dic[i][
                                      'property_id'] + """_""" + str(key) + """.} """
                for key, value in self.dic[i]["ref_dic"].items():
                    rdf_triple += """OPTIONAL { ?statement_""" + str(
                        i) + """ prov:wasDerivedFrom ?refnode_""" + str(
                        i) + """. ?refnode_""" + str(i) \
                                  + """ pr:""" + str(key) + """ ?""" + self.dic[i]['name'] + """_ref_""" + \
                                  self.dic[i][
                                      'property_id'] + """_""" + str(key) + """.} """
                rdf_triple += """OPTIONAL { ?statement_""" + str(i) + """ wikibase:rank ?""" + self.dic[i][
                    'name'] + """_rank_""" + self.dic[i]['property_id'] + """_rank. } """
            # none-verbose version
            else:
                if self.dic[i]["focus"] == "Entity ID":
                    if self.dic[i]["isSubject"]:
                        if not self.dic[i]['subclass']:
                            rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                'property_id'] + """ wdt:""" + self.dic[i][
                                              "property_id"] + """ wd:""" + self.entity_id + """. """
                        else:
                            if self.dic[i]['property_id'] == "P31":
                                rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                    'property_id'] + """ wdt:""" + self.dic[i][
                                                  "property_id"] + """ ?subclasses. """
                                rdf_triple += """?subclasses wdt:P279+ wd:""" + self.entity_id + """. """
                    else:
                        if self.dic[i]["search"] is None:
                            rdf_triple += """OPTIONAL {"""
                        rdf_triple += """wd:""" + self.entity_id + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + \
                                      self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """. """
                else:
                    if self.dic[i]["isSubject"]:
                        if not self.dic[i]['subclass']:
                            rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                'property_id'] + """ wdt:""" + self.dic[i]["property_id"] + """ ?""" + self.dic[i][
                                              'focus'] + """. """
                        else:
                            if self.dic[i]['property_id'] == "P31":
                                rdf_triple += """?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                'property_id'] + """ wdt:""" + self.dic[i]["property_id"] + """ ?subclasses. """
                                rdf_triple += """?subclasses wdt:P279+ ?""" + self.dic[i]['focus'] + """. """
                    else:
                        if self.dic[i]["search"] is None:
                            rdf_triple += """OPTIONAL {"""
                        rdf_triple += """?""" + self.dic[i]['focus'] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i][
                                          'property_id'] + """. """
            if not self.dic[i]["isSubject"]:
                if i < self.count and self.dic[i]["focus"] != self.dic[i + 1]["focus"] and self.dic[i]["search"] is None:
                    focusChanges += 1
                elif self.dic[i]["search"] is None:
                    rdf_triple += """} """
                
        for i in range(focusChanges):
            rdf_triple += """} """
        for i in range(1, self.count + 1):
            if self.dic[i]['search'] is not None and self.dic[i]["search"] != '!NA':
                if isinstance(self.dic[i]['search'], tuple):
                    if isinstance(self.dic[i]['search'][0], str):
                        rdf_triple += """FILTER (YEAR(?""" + self.dic[i]['name'] + """_""" + self.dic[i][
                            'property_id'] + """) >= """ + \
                                      self.dic[i]['search'][0] + """ && YEAR(?""" + self.dic[i]['name'] + \
                                      """_""" + self.dic[i]['property_id'] + """) <= """ + self.dic[i]['search'][
                                          1] + """) """
                    else:
                        rdf_triple += """FILTER (?""" + self.dic[i]['name'] + """_""" + self.dic[i]['property_id'] + \
                                      """ >= """ + str(self.dic[i]['search'][0]) + """ && ?""" + self.dic[i]['name'] + \
                                      """_""" + self.dic[i]['property_id'] + """ <= """ + str(
                            self.dic[i]['search'][1]) + """) """
                else:
                    rdf_triple += """FILTER (?""" + self.dic[i]['name'] + """_""" + self.dic[i][
                        'property_id'] + """ = """ + \
                                  """wd:""" + self.dic[i]['search'] + """) """
        if self.time_property is not None:
            time_filter = """?""" + self.dic[1]["name"] + """ p:""" + self.time_property + """ ?pubdateStatement.	
                          ?pubdateStatement ps:""" + self.time_property + """ ?date	
                          FILTER (YEAR(?date) = """ + self.time + """)"""
        if self.limit is not None:
            limit_statement = """LIMIT """ + str(self.limit)
        label_statement = """Service wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en" }"""
        query = """SELECT DISTINCT"""
        for i in range(1, self.count + 1):
            if self.dic[i]["rowVerbose"] or self.dic[i]["colVerbose"]:
                query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id']
                if self.dic[i]["label"]:
                    query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """Label"""
                for key, value in self.dic[i]["property_name_dic"].items():
                    query += """ ?""" + self.dic[i]["name"] + """_""" + value + """_""" + self.dic[i][
                        'property_id'] + """_""" + str(key)
                for key, value in self.dic[i]["ref_dic"].items():
                    query += """ ?""" + self.dic[i]["name"] + """_ref_""" + self.dic[i]['property_id'] + """_""" + str(
                        key)
                query += """ ?""" + self.dic[i]["name"] + """_rank_""" + self.dic[i]['property_id'] + """_rank"""
            else:
                query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id']
                if self.dic[i]["label"]:
                    query += """ ?""" + self.dic[i]["name"] + """_""" + self.dic[i]['property_id'] + """Label"""
        query += """ WHERE {""" + rdf_triple + time_filter + label_statement + """} """ + limit_statement
        return query

    def search_property_for_verbose(self):
        property_to_name = {}
        ref_to_name = {}
        rdf_triple, time_filter, limit_statement = """""", """""", """"""
        if self.dic[self.count]["rowVerbose"] or self.dic[self.count]["colVerbose"]:
            for i in range(1, self.count):
                if self.dic[i]["focus"] == "Entity ID":
                    if self.dic[i]["isSubject"]:
                        rdf_triple += """?""" + self.dic[i]["name"] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ wd:""" + self.entity_id + """ ."""
                    else:
                        rdf_triple += """wd:""" + self.entity_id + """ wdt:""" + self.dic[i]["property_id"] + """ ?""" + \
                                      self.dic[i]["name"] + """ ."""
                else:
                    last = self.dic[i]["focus"].rfind('_')
                    focus = self.dic[i]["focus"][:last]
                    if self.dic[i]["isSubject"]:
                        rdf_triple += """?""" + self.dic[i]["name"] + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + focus + """ ."""
                    else:
                        rdf_triple += """?""" + focus + """ wdt:""" + self.dic[i][
                            "property_id"] + """ ?""" + self.dic[i]["name"] + """ ."""
            if self.dic[self.count]["focus"] == "Entity ID":
                rdf_triple += """wd:""" + self.entity_id + """ p:""" + self.dic[self.count][
                    'property_id'] + """ ?statement.""" + \
                              """?statement """ + """ps:""" + self.dic[self.count]['property_id'] + """ ?item.""" + \
                              """?statement """ + """?pq """ + """?obj.""" + \
                              """?qual wikibase:qualifier ?pq.""" + \
                              """OPTIONAL{ ?statement prov:wasDerivedFrom ?refnode. ?refnode ?pr ?r.}"""
            else:
                last = self.dic[self.count]["focus"].rfind('_')
                focus = self.dic[self.count]["focus"][:last]
                rdf_triple += """?""" + focus + """ p:""" + self.dic[self.count][
                    'property_id'] + """ ?statement.""" + \
                              """?statement """ + """ps:""" + self.dic[self.count]['property_id'] + """ ?item.""" + \
                              """?statement """ + """?pq """ + """?obj.""" + \
                              """?qual wikibase:qualifier ?pq.""" + \
                              """OPTIONAL{ ?statement prov:wasDerivedFrom ?refnode. ?refnode ?pr ?r.}"""
        if self.time_property is not None:
            time_filter = """?""" + self.dic[1]["name"] + """ p:""" + self.time_property + """ ?pubdateStatement.	
                                  ?pubdateStatement ps:""" + self.time_property + """ ?date	
                                  FILTER (YEAR(?date) = """ + self.time + """)"""
        if self.limit is not None:
            limit_statement = """LIMIT """ + str(self.limit)
        label_statement = """Service wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en" }"""
        query = """SELECT DISTINCT """
        if self.dic[self.count]["rowVerbose"] or self.dic[self.count]["colVerbose"]:
            query += """?item""" + """ ?qual""" + """ ?qualLabel""" + """ ?obj """ + """?pr ?prLabel"""
            query += """ WHERE {""" + rdf_triple + time_filter + label_statement + """} """ + limit_statement
            query_result = get_results(endpoint_url, query)
            for result in query_result['results']['bindings']:
                if 'qual' in result:
                    property_to_name[result['qual']['value'].split('/')[-1]] = result['qualLabel']['value'].replace(' ',
                                                                                                                    '_')
                if 'pr' in result:
                    ref_to_name[result['pr']['value'].split('/')[-1]] = result['prLabel']['value'].replace(' ', '_')
        else:
            query += """?""" + self.dic[self.count]["name"] + """ """
        return property_to_name, ref_to_name

    def __str__(self):
        return str(self.df)

    def __getattr__(self, col_name):
        if col_name in self.df.columns:
            return self.df[col_name]
        else:
            print(col_name + " has not been found.")
            return None


def createRelation(entity_id: str, property_id=None, isSubject=None, rowVerbose=None, colVerbose=None,
                   time_property=None, time=None, name=None, label=False, limit=None, subclass=False):
    if property_id and not name:
        print("Please specify the name of the first column")
        return None
    return Relation(entity_id, property_id, isSubject, rowVerbose, colVerbose, time_property, time, name, label, limit, subclass)

def get_Firstname(name: str):
    return name.split(' ')[0]

def get_Lastname(name: str):
    return name.split(' ')[-1]

def remove_prefix(text, prefix):
    if text.startswith(prefix):
        return text[len(prefix):]
    return text


def get_results(endpoint_url, query):
    user_agent = "WDQS-example Python/%s.%s" % (sys.version_info[0], sys.version_info[1])
    # TODO adjust user agent; see https://w.wiki/CX6
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    return sparql.query().convert()


def get_name(id: str):
    query = """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#> 	
                PREFIX wd: <http://www.wikidata.org/entity/> 	
                select  *	
                where {	
                wd:""" + id + """ rdfs:label ?label .	
                FILTER (langMatches( lang(?label), "EN" ) )	
                } 	
                LIMIT 1"""
    results = get_results(endpoint_url, query)
    result = ''
    for res in results["results"]["bindings"]:
        result = res['label']['value']
    return result

In [4]:
func_lib.func_num()

4

In [5]:
def get_entity_id(url):
    return url.split('/')[-1]

func_lib.add_func(get_entity_id)

func_lib.func_num()

5

In [105]:
import requests
from bs4 import BeautifulSoup
print("100 Singers")
r = createRelation("Q177220")
r.extend("P106", 'backward', "Singer", limit=100, label=True)
r.changeFocus("Singer_P106")
r.extend("P569", 'forward', "Date_of_Birth")
r.extend("P570", 'forward', "Date_of_Death")
r.query()

def age_cal(birth, death):
    if birth == 'NA':
        return 'NA'
    if death == 'NA':  
        date_time_obj = datetime.datetime.strptime(birth[:4], '%Y')
        return datetime.datetime.now().year - date_time_obj.year
    else:
        return datetime.datetime.strptime(death[:4], '%Y').year - datetime.datetime.strptime(birth[:4], '%Y').year

r.extendWithFunction(['Date_of_Birth_P569', 'Date_of_Death_P570'], age_cal, 'Age', dim=1)
#r.extendWithFunction('Singer_P106Label',textual_summary,'summary')
# for index, row in r.df.iterrows():
#     print(row['summary'])
r.df

100 Singers


Entity ID  \
0   http://www.wikidata.org/entity/Q177220   
1   http://www.wikidata.org/entity/Q177220   
2   http://www.wikidata.org/entity/Q177220   
3   http://www.wikidata.org/entity/Q177220   
4   http://www.wikidata.org/entity/Q177220   
5   http://www.wikidata.org/entity/Q177220   
6   http://www.wikidata.org/entity/Q177220   
7   http://www.wikidata.org/entity/Q177220   
8   http://www.wikidata.org/entity/Q177220   
9   http://www.wikidata.org/entity/Q177220   
10  http://www.wikidata.org/entity/Q177220   
11  http://www.wikidata.org/entity/Q177220   
12  http://www.wikidata.org/entity/Q177220   
13  http://www.wikidata.org/entity/Q177220   
14  http://www.wikidata.org/entity/Q177220   
15  http://www.wikidata.org/entity/Q177220   
16  http://www.wikidata.org/entity/Q177220   
17  http://www.wikidata.org/entity/Q177220   
18  http://www.wikidata.org/entity/Q177220   
19  http://www.wikidata.org/entity/Q177220   
20  http://www.wikidata.org/entity/Q177220   
21  http://www.wikidata.org/entity/Q177220   
22  http://www.wikidata.org/entity/Q177220   
23  http://www.wikidata.org/entity/Q177220   
24  http://www.wikidata.org/entity/Q177220   
25  http://www.wikidata.org/entity/Q177220   
26  http://www.wikidata.org/entity/Q177220   
27  http://www.wikidata.org/entity/Q177220   
28  http://www.wikidata.org/entity/Q177220   
29  http://www.wikidata.org/entity/Q177220   
30  http://www.wikidata.org/entity/Q177220   
31  http://www.wikidata.org/entity/Q177220   
32  http://www.wikidata.org/entity/Q177220   
33  http://www.wikidata.org/entity/Q177220   
34  http://www.wikidata.org/entity/Q177220   
35  http://www.wikidata.org/entity/Q177220   
36  http://www.wikidata.org/entity/Q177220   
37  http://www.wikidata.org/entity/Q177220   
38  http://www.wikidata.org/entity/Q177220   
39  http://www.wikidata.org/entity/Q177220   
40  http://www.wikidata.org/entity/Q177220   
41  http://www.wikidata.org/entity/Q177220   
42  http://www.wikidata.org/entity/Q177220   
43  http://www.wikidata.org/entity/Q177220   
44  http://www.wikidata.org/entity/Q177220   
45  http://www.wikidata.org/entity/Q177220   
46  http://www.wikidata.org/entity/Q177220   
47  http://www.wikidata.org/entity/Q177220   
48  http://www.wikidata.org/entity/Q177220   
49  http://www.wikidata.org/entity/Q177220   
50  http://www.wikidata.org/entity/Q177220   
51  http://www.wikidata.org/entity/Q177220   
52  http://www.wikidata.org/entity/Q177220   
53  http://www.wikidata.org/entity/Q177220   
54  http://www.wikidata.org/entity/Q177220   
55  http://www.wikidata.org/entity/Q177220   
56  http://www.wikidata.org/entity/Q177220   
57  http://www.wikidata.org/entity/Q177220   
58  http://www.wikidata.org/entity/Q177220   
59  http://www.wikidata.org/entity/Q177220   
60  http://www.wikidata.org/entity/Q177220   
61  http://www.wikidata.org/entity/Q177220   
62  http://www.wikidata.org/entity/Q177220   
63  http://www.wikidata.org/entity/Q177220   
64  http://www.wikidata.org/entity/Q177220   
65  http://www.wikidata.org/entity/Q177220   
66  http://www.wikidata.org/entity/Q177220   
67  http://www.wikidata.org/entity/Q177220   
68  http://www.wikidata.org/entity/Q177220   
69  http://www.wikidata.org/entity/Q177220   
70  http://www.wikidata.org/entity/Q177220   
71  http://www.wikidata.org/entity/Q177220   
72  http://www.wikidata.org/entity/Q177220   
73  http://www.wikidata.org/entity/Q177220   
74  http://www.wikidata.org/entity/Q177220   
75  http://www.wikidata.org/entity/Q177220   
76  http://www.wikidata.org/entity/Q177220   
77  http://www.wikidata.org/entity/Q177220   
78  http://www.wikidata.org/entity/Q177220   
79  http://www.wikidata.org/entity/Q177220   
80  http://www.wikidata.org/entity/Q177220   
81  http://www.wikidata.org/entity/Q177220   
82  http://www.wikidata.org/entity/Q177220   
83  http://www.wikidata.org/entity/Q177220   
84  http://www.wikidata.org/entity/Q177220   
85  http://www.wikidata.org/entity/Q177220   
86  http://www.wikidata.org/ent

In [6]:
func_lib.func_num()

7

In [95]:
import requests, json

film_gross = pd.read_csv('boxoffice.csv')

def map(x):
    if x == 'NA':
        return 'NA'
    info = requests.get('http://ipinfo.io/json').json()
    url = 'https://www.google.com/maps/dir/'
    url += info['city'] + '/'
    url += x
    url.replace(' ', '+')
    url.replace('&', '%26')
    r = requests.get(url)
    return r.url


def share(df, name, film, director, film_gross):
    #film_gross = pd.read_csv('boxoffice.csv')
    film_gross.columns = ['rank', film, 'studio', 'gross', 'year']
    film_gross[film] = film_gross[film].astype(str)
    df[film] = df[film].astype(str)
    new_df = film_gross.merge(df, on=film)  # merge with external data
    new_df.drop_duplicates(subset=['rank'], inplace=True)
    sum_df = new_df.groupby([director]).sum()
    sum_df.columns = ['rk', 'total', 'y']
    final_df = new_df.merge(sum_df, on=director)
    final_df[name] = final_df.apply(lambda x: '%.2f%%' % (x['gross'] / x['total'] * 100), axis=1)
    sel = [str(x) for x in df.columns]
    sel.append(name)
    return final_df[sel]

In [96]:
r3 = createRelation('Q2526255')
r3.extend('P106', 'backward', 'Directors', label=True)
r3.changeFocus('Directors_P106')
r3.extend('P57', 'backward', 'Films', label=True)
r3.changeFocus('Films_P57')
r3.extend('P577', 'forward', 'Time', search=('2015', '2020'))
r3.query()
r3.extendWithFunction(columns=['Films_P57Label', 'Directors_P106Label'],
                      func=share, name='fraction', param=film_gross)
r3.df

Entity ID  \
0     http://www.wikidata.org/entity/Q2526255   
1     http://www.wikidata.org/entity/Q2526255   
2     http://www.wikidata.org/entity/Q2526255   
3     http://www.wikidata.org/entity/Q2526255   
4     http://www.wikidata.org/entity/Q2526255   
5     http://www.wikidata.org/entity/Q2526255   
6     http://www.wikidata.org/entity/Q2526255   
7     http://www.wikidata.org/entity/Q2526255   
8     http://www.wikidata.org/entity/Q2526255   
9     http://www.wikidata.org/entity/Q2526255   
10    http://www.wikidata.org/entity/Q2526255   
11    http://www.wikidata.org/entity/Q2526255   
12    http://www.wikidata.org/entity/Q2526255   
13    http://www.wikidata.org/entity/Q2526255   
14    http://www.wikidata.org/entity/Q2526255   
15    http://www.wikidata.org/entity/Q2526255   
16    http://www.wikidata.org/entity/Q2526255   
17    http://www.wikidata.org/entity/Q2526255   
18    http://www.wikidata.org/entity/Q2526255   
19    http://www.wikidata.org/entity/Q2526255   
20    http://www.wikidata.org/entity/Q2526255   
21    http://www.wikidata.org/entity/Q2526255   
22    http://www.wikidata.org/entity/Q2526255   
23    http://www.wikidata.org/entity/Q2526255   
24    http://www.wikidata.org/entity/Q2526255   
25    http://www.wikidata.org/entity/Q2526255   
26    http://www.wikidata.org/entity/Q2526255   
27    http://www.wikidata.org/entity/Q2526255   
28    http://www.wikidata.org/entity/Q2526255   
29    http://www.wikidata.org/entity/Q2526255   
30    http://www.wikidata.org/entity/Q2526255   
31    http://www.wikidata.org/entity/Q2526255   
32    http://www.wikidata.org/entity/Q2526255   
33    http://www.wikidata.org/entity/Q2526255   
34    http://www.wikidata.org/entity/Q2526255   
35    http://www.wikidata.org/entity/Q2526255   
36    http://www.wikidata.org/entity/Q2526255   
37    http://www.wikidata.org/entity/Q2526255   
38    http://www.wikidata.org/entity/Q2526255   
39    http://www.wikidata.org/entity/Q2526255   
40    http://www.wikidata.org/entity/Q2526255   
41    http://www.wikidata.org/entity/Q2526255   
42    http://www.wikidata.org/entity/Q2526255   
43    http://www.wikidata.org/entity/Q2526255   
44    http://www.wikidata.org/entity/Q2526255   
45    http://www.wikidata.org/entity/Q2526255   
46    http://www.wikidata.org/entity/Q2526255   
47    http://www.wikidata.org/entity/Q2526255   
48    http://www.wikidata.org/entity/Q2526255   
49    http://www.wikidata.org/entity/Q2526255   
50    http://www.wikidata.org/entity/Q2526255   
51    http://www.wikidata.org/entity/Q2526255   
52    http://www.wikidata.org/entity/Q2526255   
53    http://www.wikidata.org/entity/Q2526255   
54    http://www.wikidata.org/entity/Q2526255   
55    http://www.wikidata.org/entity/Q2526255   
56    http://www.wikidata.org/entity/Q2526255   
57    http://www.wikidata.org/entity/Q2526255   
58    http://www.wikidata.org/entity/Q2526255   
59    http://www.wikidata.org/entity/Q2526255   
60    http://www.wikidata.org/entity/Q2526255   
61    http://www.wikidata.org/entity/Q2526255   
62    http://www.wikidata.org/entity/Q2526255   
63    http://www.wikidata.org/entity/Q2526255   
64    http://www.wikidata.org/entity/Q2526255   
65    http://www.wikidata.org/entity/Q2526255   
66    http://www.wikidata.org/entity/Q2526255   
67    http://www.wikidata.org/entity/Q2526255   
68    http://www.wikidata.org/entity/Q2526255   
69    http://www.wikidata.org/entity/Q2526255   
70    http://www.wikidata.org/entity/Q2526255   
71    http://www.wikidata.org/entity/Q2526255   
72    http://www.wikidata.org/entity/Q2526255   
73    http://www.wikidata.org/entity/Q2526255   
74    http://www.wikidata.org/entity/Q2526255   
75    http://www.wikidata.org/entity/Q2526255   
76    http://www.wikidata.org/entity/Q2526255   
77    http://www.wikidata.org/entity/Q2526255   
78    http://www.wikidata.org/entity/Q2526255   
79    http://www.wikidata.org/entity/Q2526255   
80    http://www.wikidata.org/entity/Q2526255   
81    http://www.w

In [5]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 100)
r3.df

Empty DataFrame
Columns: []
Index: []

In [97]:
r4 = createRelation('Q33999')
r4.extend('P106', 'backward', 'Actors', label=True)
r4.changeFocus('Actors_P106')
r4.extend('P161', 'backward', 'Films', label=True)
r4.changeFocus('Films_P161')
r4.extend('P577', 'forward', 'Time', search=('2010', '2020'), limit=2000)
r4.query()
r4.extendWithFunction(columns=['Films_P161Label', 'Actors_P106Label'], func=share, name='fraction', param=film_gross)
r4.df

Entity ID  \
0    http://www.wikidata.org/entity/Q33999   
1    http://www.wikidata.org/entity/Q33999   
2    http://www.wikidata.org/entity/Q33999   
3    http://www.wikidata.org/entity/Q33999   
4    http://www.wikidata.org/entity/Q33999   
5    http://www.wikidata.org/entity/Q33999   
6    http://www.wikidata.org/entity/Q33999   
7    http://www.wikidata.org/entity/Q33999   
8    http://www.wikidata.org/entity/Q33999   
9    http://www.wikidata.org/entity/Q33999   
10   http://www.wikidata.org/entity/Q33999   
11   http://www.wikidata.org/entity/Q33999   
12   http://www.wikidata.org/entity/Q33999   
13   http://www.wikidata.org/entity/Q33999   
14   http://www.wikidata.org/entity/Q33999   
15   http://www.wikidata.org/entity/Q33999   
16   http://www.wikidata.org/entity/Q33999   
17   http://www.wikidata.org/entity/Q33999   
18   http://www.wikidata.org/entity/Q33999   
19   http://www.wikidata.org/entity/Q33999   
20   http://www.wikidata.org/entity/Q33999   
21   http://www.wikidata.org/entity/Q33999   
22   http://www.wikidata.org/entity/Q33999   
23   http://www.wikidata.org/entity/Q33999   
24   http://www.wikidata.org/entity/Q33999   
25   http://www.wikidata.org/entity/Q33999   
26   http://www.wikidata.org/entity/Q33999   
27   http://www.wikidata.org/entity/Q33999   
28   http://www.wikidata.org/entity/Q33999   
29   http://www.wikidata.org/entity/Q33999   
30   http://www.wikidata.org/entity/Q33999   
31   http://www.wikidata.org/entity/Q33999   
32   http://www.wikidata.org/entity/Q33999   
33   http://www.wikidata.org/entity/Q33999   
34   http://www.wikidata.org/entity/Q33999   
35   http://www.wikidata.org/entity/Q33999   
36   http://www.wikidata.org/entity/Q33999   
37   http://www.wikidata.org/entity/Q33999   
38   http://www.wikidata.org/entity/Q33999   
39   http://www.wikidata.org/entity/Q33999   
40   http://www.wikidata.org/entity/Q33999   
41   http://www.wikidata.org/entity/Q33999   
42   http://www.wikidata.org/entity/Q33999   
43   http://www.wikidata.org/entity/Q33999   
44   http://www.wikidata.org/entity/Q33999   
45   http://www.wikidata.org/entity/Q33999   
46   http://www.wikidata.org/entity/Q33999   
47   http://www.wikidata.org/entity/Q33999   
48   http://www.wikidata.org/entity/Q33999   
49   http://www.wikidata.org/entity/Q33999   
50   http://www.wikidata.org/entity/Q33999   
51   http://www.wikidata.org/entity/Q33999   
52   http://www.wikidata.org/entity/Q33999   
53   http://www.wikidata.org/entity/Q33999   
54   http://www.wikidata.org/entity/Q33999   
55   http://www.wikidata.org/entity/Q33999   
56   http://www.wikidata.org/entity/Q33999   
57   http://www.wikidata.org/entity/Q33999   
58   http://www.wikidata.org/entity/Q33999   
59   http://www.wikidata.org/entity/Q33999   
60   http://www.wikidata.org/entity/Q33999   
61   http://www.wikidata.org/entity/Q33999   
62   http://www.wikidata.org/entity/Q33999   
63   http://www.wikidata.org/entity/Q33999   
64   http://www.wikidata.org/entity/Q33999   
65   http://www.wikidata.org/entity/Q33999   
66   http://www.wikidata.org/entity/Q33999   
67   http://www.wikidata.org/entity/Q33999   
68   http://www.wikidata.org/entity/Q33999   
69   http://www.wikidata.org/entity/Q33999   
70   http://www.wikidata.org/entity/Q33999   
71   http://www.wikidata.org/entity/Q33999   
72   http://www.wikidata.org/entity/Q33999   
73   http://www.wikidata.org/entity/Q33999   
74   http://www.wikidata.org/entity/Q33999   
75   http://www.wikidata.org/entity/Q33999   
76   http://www.wikidata.org/entity/Q33999   
77   http://www.wikidata.org/entity/Q33999   
78   http://www.wikidata.org/entity/Q33999   
79   http://www.wikidata.org/entity/Q33999   
80   http://www.wikidata.org/entity/Q33999   
81   http://www.wikidata.org/entity/Q33999   
82   http://www.wikidata.org/entity/Q33999   
83   http://www.wikidata.org/entity/Q33999   
84   http://www.wikidata.org/entity/Q33999   
85   http://www.wikidata.org/entity/Q33999   
86   http://www.wikidata.org/en

In [22]:
r6 = createRelation("Q11696")
r6.extend("P39", True, "Presidents")
r6.changeFocus("Presidents_P39")
r6.extend("P19", False, "place_president", label=True)
r6.query()
r6.extend("P26", False, "Spouse")
r6.changeFocus("Spouse_P26")
r6.extend("P19", False, "place_spouse", label=True)
r6.query()
r6.extendWithFunction("place_president_P19Label", map, "to_president")
r6.extendWithFunction("place_spouse_P19Label", map, "to_spouse")
r6.df

Entity ID  \
0   http://www.wikidata.org/entity/Q11696   
1   http://www.wikidata.org/entity/Q11696   
2   http://www.wikidata.org/entity/Q11696   
3   http://www.wikidata.org/entity/Q11696   
4   http://www.wikidata.org/entity/Q11696   
..                                    ...   
65  http://www.wikidata.org/entity/Q11696   
66  http://www.wikidata.org/entity/Q11696   
67  http://www.wikidata.org/entity/Q11696   
68  http://www.wikidata.org/entity/Q11696   
69  http://www.wikidata.org/entity/Q11696   

                             Presidents_P39  \
0    http://www.wikidata.org/entity/Q608408   
1   http://www.wikidata.org/entity/Q1052076   
2   http://www.wikidata.org/entity/Q2719854   
3   http://www.wikidata.org/entity/Q3438922   
4   http://www.wikidata.org/entity/Q3545001   
..                                      ...   
65    http://www.wikidata.org/entity/Q11813   
66    http://www.wikidata.org/entity/Q11869   
67     http://www.wikidata.org/entity/Q9640   
68    http://www.wikidata.org/entity/Q35498   
69    http://www.wikidata.org/entity/Q11815   

                         place_president_P19 place_president_P19Label  \
0                                         NA                       NA   
1                                         NA                       NA   
2                                         NA                       NA   
3                                         NA                       NA   
4                                         NA                       NA   
..                                       ...                      ...   
65   http://www.wikidata.org/entity/Q1375967              Port Conway   
66    http://www.wikidata.org/entity/Q337348      Charles City County   
67    http://www.wikidata.org/entity/Q975048                Stonewall   
68   http://www.wikidata.org/entity/Q1393235                Fairfield   
69  http://www.wikidata.org/entity/Q14712874              Monroe Hall   

                                 Spouse_P26  \
0                                        NA   
1                                        NA   
2                                        NA   
3                                        NA   
4                                        NA   
..                                      ...   
65   http://www.wikidata.org/entity/Q233638   
66   http://www.wikidata.org/entity/Q255190   
67   http://www.wikidata.org/entity/Q233648   
68  http://www.wikidata.org/entity/Q2306099   
69   http://www.wikidata.org/entity/Q233628   

                           place_spouse_P19 place_spouse_P19Label  \
0                                        NA                    NA   
1                                        NA                    NA   
2                                        NA                    NA   
3                                        NA                    NA   
4                                        NA                    NA   
..                                      ...                   ...   
65   http://www.wikidata.org/entity/Q502257       Guilford County   
66   http://www.wikidata.org/entity/Q962499            Morristown   
67  http://www.wikidata.org/entity/Q3476511               Karnack   
68   http://www.wikidata.org/entity/Q990985              Culpeper   
69       http://www.wikidata.org/entity/Q60         New York City   

                                         to_president  \
0                                                  NA   
1                                                  NA   
2                                                  NA   
3                                                  NA   
4                                                  NA   
..                                                ...   
65  https://www.google.com/maps/dir/Ann%20Arbor/Po...   
66  https://www.google.com/maps/dir/Ann%20Arbor/Ch...   
67  https://www.google.com/maps/dir/Ann%20Arbor/St...   
68  https://www.google.com/maps/dir/Ann%20Arbor/Fa...   
69  https://www.google.com/m

In [115]:
def growth_rate(df, name, gdp, time):
    df.sort_values(by=[time], ascending=False, inplace=True)
    df.reset_index(drop=True, inplace=True)
    df[name] = df[gdp]
    for i in range(len(df)-1):
        df.loc[i, name] = '%.2f%%' % ((float(df.loc[i, gdp]) - float(df.loc[i+1, gdp])) / float(df.loc[i+1, gdp]) * 100)
    df.loc[len(df)-1, name] = 'NA'
    return df

r = createRelation("Q458")
r.extend("P2131", 'forward', "GDP", rowVerbose=True, colVerbose=True)
r.query()
r.extendWithFunction(['GDP_P2131', 'GDP_point_in_time_P2131_P585'], growth_rate, 'growth_rate')

In [116]:
r.df

Entity ID         GDP_P2131  \
0   http://www.wikidata.org/entity/Q458    17277697660475   
1   http://www.wikidata.org/entity/Q458  16491855791194.9   
2   http://www.wikidata.org/entity/Q458  16416670356766.4   
3   http://www.wikidata.org/entity/Q458  18635535561984.7   
4   http://www.wikidata.org/entity/Q458  18029679886231.6   
5   http://www.wikidata.org/entity/Q458  17292774157162.6   
6   http://www.wikidata.org/entity/Q458    18350556736022   
7   http://www.wikidata.org/entity/Q458  16987391593239.7   
8   http://www.wikidata.org/entity/Q458  17102490228101.1   
9   http://www.wikidata.org/entity/Q458  19137013228474.8   
10  http://www.wikidata.org/entity/Q458  17793784213095.4   
11  http://www.wikidata.org/entity/Q458  15398749328298.7   
12  http://www.wikidata.org/entity/Q458  14433470312804.2   
13  http://www.wikidata.org/entity/Q458  13798204365627.7   
14  http://www.wikidata.org/entity/Q458  11949502573497.4   
15  http://www.wikidata.org/entity/Q458  9816570308921.34   
16  http://www.wikidata.org/entity/Q458  9004047000477.56   
17  http://www.wikidata.org/entity/Q458   8906259675838.6   
18  http://www.wikidata.org/entity/Q458  9583222954183.93   
19  http://www.wikidata.org/entity/Q458  9597916593883.38   
20  http://www.wikidata.org/entity/Q458  9281691729773.42   
21  http://www.wikidata.org/entity/Q458  9832779726332.57   
22  http://www.wikidata.org/entity/Q458  9617626658380.63   
23  http://www.wikidata.org/entity/Q458  8291509307136.46   
24  http://www.wikidata.org/entity/Q458  7808204288725.23   
25  http://www.wikidata.org/entity/Q458  8563868132607.11   
26  http://www.wikidata.org/entity/Q458   7859432403021.2   
27  http://www.wikidata.org/entity/Q458  7573007883964.69   
28  http://www.wikidata.org/entity/Q458  6107077077923.22   
29  http://www.wikidata.org/entity/Q458  5981271674728.67   
30  http://www.wikidata.org/entity/Q458  5362160463594.03   
31  http://www.wikidata.org/entity/Q458  4333946473357.81   
32  http://www.wikidata.org/entity/Q458  3160727474313.24   
33  http://www.wikidata.org/entity/Q458   3058273854701.5   
34  http://www.wikidata.org/entity/Q458   3185259544963.1   
35  http://www.wikidata.org/entity/Q458  3286230902571.68   
36  http://www.wikidata.org/entity/Q458  3414523775281.61   
37  http://www.wikidata.org/entity/Q458  3859034986977.15   
38  http://www.wikidata.org/entity/Q458  3381002006988.18   
39  http://www.wikidata.org/entity/Q458  2768458431504.73   
40  http://www.wikidata.org/entity/Q458  2259061132562.77   
41  http://www.wikidata.org/entity/Q458   1994811570691.8   
42  http://www.wikidata.org/entity/Q458  1925962407817.74   
43  http://www.wikidata.org/entity/Q458  1652067527870.01   
44  http://www.wikidata.org/entity/Q458  1469889521862.17   
45  http://www.wikidata.org/entity/Q458   1157617173702.1   
46  http://www.wikidata.org/entity/Q458  966895024360.652   
47  http://www.wikidata.org/entity/Q458  854806976544.551   
48  http://www.wikidata.org/entity/Q458  754985079762.717   
49  http://www.wikidata.org/entity/Q458  687385494341.584   
50  http://www.wikidata.org/entity/Q458  661332223545.931   
51  http://www.wikidata.org/entity/Q458  615437686396.201   
52  http://www.wikidata.org/entity/Q458  567732375288.191   
53  http://www.wikidata.org/entity/Q458  521327946897.929   
54  http://www.wikidata.org/entity/Q458  470414635948.368   
55  http://www.wikidata.org/entity/Q458  427014890429.994   
56  http://www.wikidata.org/entity/Q458   390887213480.75   
57  http://www.wikidata.org/entity/Q458  359029375700.783   

                        GDP_rank_P2131_rank GDP_point_in_time_P2131_P585  \
0   http://wikiba.se/ontology#PreferredRank         2017-01-01T00:00:00Z   
1      http://wikiba.se/ontology#NormalRank         2016-01-01T00:00:00Z   
2      http://wikiba.se/ontology#NormalRank         2015-01-01T00:00:00Z   
3      http://wikiba.se/ontology#NormalRank         2014-01-01T00:00:00Z   
4      http://wikiba.se/ontology#NormalRank       

In [117]:
r2 = createRelation('Q30')
r2.extend('P6', 'forward', 'president', rowVerbose=True, colVerbose=True, label=True)
r2.extend('P2131', 'forward', 'gdp', rowVerbose=True, colVerbose=True)
r2.query()
r2.df

Entity ID  \
0     http://www.wikidata.org/entity/Q30   
1     http://www.wikidata.org/entity/Q30   
2     http://www.wikidata.org/entity/Q30   
3     http://www.wikidata.org/entity/Q30   
4     http://www.wikidata.org/entity/Q30   
5     http://www.wikidata.org/entity/Q30   
6     http://www.wikidata.org/entity/Q30   
7     http://www.wikidata.org/entity/Q30   
8     http://www.wikidata.org/entity/Q30   
9     http://www.wikidata.org/entity/Q30   
10    http://www.wikidata.org/entity/Q30   
11    http://www.wikidata.org/entity/Q30   
12    http://www.wikidata.org/entity/Q30   
13    http://www.wikidata.org/entity/Q30   
14    http://www.wikidata.org/entity/Q30   
15    http://www.wikidata.org/entity/Q30   
16    http://www.wikidata.org/entity/Q30   
17    http://www.wikidata.org/entity/Q30   
18    http://www.wikidata.org/entity/Q30   
19    http://www.wikidata.org/entity/Q30   
20    http://www.wikidata.org/entity/Q30   
21    http://www.wikidata.org/entity/Q30   
22    http://www.wikidata.org/entity/Q30   
23    http://www.wikidata.org/entity/Q30   
24    http://www.wikidata.org/entity/Q30   
25    http://www.wikidata.org/entity/Q30   
26    http://www.wikidata.org/entity/Q30   
27    http://www.wikidata.org/entity/Q30   
28    http://www.wikidata.org/entity/Q30   
29    http://www.wikidata.org/entity/Q30   
30    http://www.wikidata.org/entity/Q30   
31    http://www.wikidata.org/entity/Q30   
32    http://www.wikidata.org/entity/Q30   
33    http://www.wikidata.org/entity/Q30   
34    http://www.wikidata.org/entity/Q30   
35    http://www.wikidata.org/entity/Q30   
36    http://www.wikidata.org/entity/Q30   
37    http://www.wikidata.org/entity/Q30   
38    http://www.wikidata.org/entity/Q30   
39    http://www.wikidata.org/entity/Q30   
40    http://www.wikidata.org/entity/Q30   
41    http://www.wikidata.org/entity/Q30   
42    http://www.wikidata.org/entity/Q30   
43    http://www.wikidata.org/entity/Q30   
44    http://www.wikidata.org/entity/Q30   
45    http://www.wikidata.org/entity/Q30   
46    http://www.wikidata.org/entity/Q30   
47    http://www.wikidata.org/entity/Q30   
48    http://www.wikidata.org/entity/Q30   
49    http://www.wikidata.org/entity/Q30   
50    http://www.wikidata.org/entity/Q30   
51    http://www.wikidata.org/entity/Q30   
52    http://www.wikidata.org/entity/Q30   
53    http://www.wikidata.org/entity/Q30   
54    http://www.wikidata.org/entity/Q30   
55    http://www.wikidata.org/entity/Q30   
56    http://www.wikidata.org/entity/Q30   
57    http://www.wikidata.org/entity/Q30   
58    http://www.wikidata.org/entity/Q30   
59    http://www.wikidata.org/entity/Q30   
60    http://www.wikidata.org/entity/Q30   
61    http://www.wikidata.org/entity/Q30   
62    http://www.wikidata.org/entity/Q30   
63    http://www.wikidata.org/entity/Q30   
64    http://www.wikidata.org/entity/Q30   
65    http://www.wikidata.org/entity/Q30   
66    http://www.wikidata.org/entity/Q30   
67    http://www.wikidata.org/entity/Q30   
68    http://www.wikidata.org/entity/Q30   
69    http://www.wikidata.org/entity/Q30   
70    http://www.wikidata.org/entity/Q30   
71    http://www.wikidata.org/entity/Q30   
72    http://www.wikidata.org/entity/Q30   
73    http://www.wikidata.org/entity/Q30   
74    http://www.wikidata.org/entity/Q30   
75    http://www.wikidata.org/entity/Q30   
76    http://www.wikidata.org/entity/Q30   
77    http://www.wikidata.org/entity/Q30   
78    http://www.wikidata.org/entity/Q30   
79    http://www.wikidata.org/entity/Q30   
80    http://www.wikidata.org/entity/Q30   
81    http://www.wikidata.org/entity/Q30   
82    http://www.wikidata.org/entity/Q30   
83    http://www.wikidata.org/entity/Q30   
84    http://www.wikidata.org/entity/Q30   
85    http://www.wikidata.org/entity/Q30   
86    http://www.wikidata.org/entity/Q30   
87    http://www.wikidata.org/entity/Q30   
88    http://www.wikidata.org/entity/Q30   
89    http://www.wikidata.org/entity/Q30   
90    http://www.wikidata.o

In [131]:
# def match(df, name, gtime, start, end):
#     df = df.query(str(str(gtime) >= str(start)))
#     return df

r2.df['gdp_point_in_time_P2131_P585'] = r2.df['gdp_point_in_time_P2131_P585'][:4]
r2.df['president_start_time_P6_P580'] = r2.df['president_start_time_P6_P580'][:4]
r2.df['president_end_time_P6_P582'] = r2.df['president_end_time_P6_P582'][:4]
#r2.extendWithFunction(['gdp_point_in_time_P2131_P585', 'president_start_time_P6_P580', 'president_end_time_P6_P582'], match, 'm')


def growth(df, name, pres, gdp):
    df = df[[pres, gdp]]
